In [1]:
import os
# os.environ['CUDA_VISIBLE_DEVICES'] = "0,1,2,3"

In [62]:
import torch
import pickle
import numpy as np
from verl.utils import hf_tokenizer
from verl.utils.torch_functional import logprobs_from_logits
from pprint import pprint

import tqdm

tokenizer = hf_tokenizer("qwen/qwen2.5-7b-instruct", is_instruct_model=True, trust_remote_code=True)

data = [[pickle.load(open(f"temp_worldsize_4_rank_{gpu_idx}_index_{step}.pkl", 'rb')) for gpu_idx in [0,1,2,3]]
        for step in range(1)]
data_og_batches = [[d[0] for d in data_el] for data_el in data]
data_split_micro_batches = [[d[1] for d in data_el] for data_el in data]

In [63]:
# agent_data = [[pickle.load(open(f"../verl-agent/temp_worldsize_4_rank_{gpu_idx}_index_{step}.pkl", 'rb')) for gpu_idx in [0,1,2,3]]
#         for step in range(1)]
# agent_data_og_batches = [[d[0] for d in data_el] for data_el in agent_data]
# agent_data_split_micro_batches = [[d[1] for d in data_el] for data_el in agent_data]


# len(agent_data[0][0])
# # [[agent_data[0][0][0].to('cpu'), agent_data[0][0][1]]]
# new_data_on_cpu = [[[agent_data_not_tuple.to('cpu'), [s.to('cpu') for s in agent_data_tuple]] for agent_data_not_tuple, agent_data_tuple in agent_data[0]]]
# import pickle
# pickle.dump(new_data_on_cpu, open("agent_data.pkl", 'wb'))

agent_data = pickle.load(open('agent_data.pkl', 'rb'))
agent_data_og_batches = [[d[0] for d in data_el] for data_el in agent_data]
agent_data_split_micro_batches = [[d[1] for d in data_el] for data_el in agent_data]

In [64]:
# combining the data to one dataproto object, and 
# check the sequences which are non terminal and their rewards. [this looks good they terminate at 15 interactions, which is ok as it should happen with verl-agent]
#   TODO: This should be fixed tho according to DAPO
# check the reward terms from the sequences which are 
from verl import DataProto
from collections import Counter

full_data = DataProto.concat(data_og_batches[0])

full_data.batch.keys()
# ['attention_mask', 'advantages', 'input_ids', 'token_level_scores', 
# 'old_log_probs', 'returns', 'token_level_rewards', 'ref_log_prob', 
# 'position_ids', 'responses', 'response_mask', 'loss_mask', 'prompts']
full_data.non_tensor_batch.keys()
# ['data_source', 'ability', 'reward_model', 'extra_info', 'index', 'uid', 
# 'messages', 'reward_scores', 'request_ids', 'context_indices', 'to_log_stats']

# need to get the full input ids which correspond to the same request_ids, 
# and order them by context_indices and then print with the correct tokenizer
full_traj_responses = [""] * len(full_data)
full_traj_response_text_map = dict()
traj_lens = []
for i, response_id in enumerate(full_data.non_tensor_batch['request_ids']):
    if response_id in full_traj_response_text_map:
        full_traj_responses[i] = full_traj_response_text_map[response_id]
        continue
    indicies_of_traj = [j for j, res_id in enumerate(full_data.non_tensor_batch['request_ids']) if res_id == response_id]
    indicies_of_traj.sort(key=lambda el: full_data.non_tensor_batch['context_indices'][el])
    traj_lens.append(len(indicies_of_traj))
    full_traj_responses[i] = "\n==========================\n".join((tokenizer.decode(full_data.batch['input_ids'][index_of_traj][full_data.batch['attention_mask'][index_of_traj] == 1], skip_special_tokens=False) for j, index_of_traj in enumerate(indicies_of_traj)))
    full_traj_response_text_map[response_id] = full_traj_responses[i]
full_data.non_tensor_batch['full_traj_response'] = full_traj_responses

In [68]:
pprint(list(set(full_traj_responses)))

['<|im_start|>system\n'
 'You will determine the correct combination of characters at [Position 1, '
 'Position 2, Position 3] in a 3-character combination lock through iterative '
 'reasoning and queries.\n'
 'All 3 characters are unique.\n'
 "The set of valid characters are as follows: ['0', '1', '2', '3', '4', '5', "
 "'6', '7', '8', '9']\n"
 "Each action is a query of the form ['char 1', 'char 2', 'char 3'].\n"
 'Each time you query a combination, you will get feedback from the user about '
 'each character: either not in the combination, in the combination but in a '
 'different position, or in the combination and in the right position.\n'
 'You can make up to 12 queries.\n'
 'Your goal is to find the correct combination in the least number of '
 'queries.<|im_end|>\n'
 '<|im_start|>user\n'
 'Give me your first query formatted as a list of 3 characters inside <action> '
 '... </action> after thinking inside <think> ... </think>, e.g., <think> '
 "Let's think step by step before gi

In [66]:
from verl import DataProto
from collections import Counter

agent_full_data = DataProto.concat(agent_data_og_batches[0])

agent_full_data.batch.keys()
# ['position_ids', 'prompts', 'responses', 'rollout_log_probs', 'token_level_scores', 
#  'token_level_rewards', 'advantages', 'returns', 'attention_mask', 'ref_log_prob', 
#  'response_mask', 'input_ids', 'old_log_probs']
agent_full_data.non_tensor_batch.keys()
# ['anchor_obs', 'index', 'data_source', 'uid', 'traj_uid', 'raw_prompt', 'is_action_valid', 
#  'rewards', 'active_masks', 'text_actions', 'step', 'episode_rewards', 'episode_rewards_mean', 
#  'episode_rewards_min', 'episode_rewards_max', 'episode_lengths', 'episode_lengths_mean', 
#  'episode_lengths_min', 'episode_lengths_max', 'success_rate', 
#  'action_generation_failures_success_rate', 'belief_generation_failures_success_rate', 
#  'non_terminal_trajectories_success_rate']

# need to get the full input ids which correspond to the same request_ids, 
# and order them by context_indices and then print with the correct tokenizer
agent_full_traj_responses = [""] * len(agent_full_data)
agent_full_traj_response_text_map = dict()
agent_traj_lens = []
for i, response_id in enumerate(agent_full_data.non_tensor_batch['traj_uid']):
    if response_id in agent_full_traj_response_text_map:
        agent_full_traj_responses[i] = agent_full_traj_response_text_map[response_id]
        continue
    indicies_of_traj = [j for j, res_id in enumerate(agent_full_data.non_tensor_batch['traj_uid']) if res_id == response_id]
    # print(indicies_of_traj)
    indicies_of_traj.sort(key=lambda el: agent_full_data.non_tensor_batch['step'][el])
    # print(indicies_of_traj)
    all_steps = [agent_full_data.non_tensor_batch['step'][j].item() for j in indicies_of_traj]
    agent_traj_lens.append(len(set(all_steps)))
    agent_full_traj_responses[i] = "\n==========================\n".join((tokenizer.decode(agent_full_data.batch['input_ids'][index_of_traj][agent_full_data.batch['attention_mask'][index_of_traj] == 1], skip_special_tokens=False) for j, index_of_traj in enumerate(indicies_of_traj)))
    agent_full_traj_response_text_map[response_id] = agent_full_traj_responses[i]
    # print(agent_full_traj_responses[i])
    # print(response_id)
    # # if i > 400:
    #     break

agent_full_data.non_tensor_batch['full_traj_response'] = agent_full_traj_responses



In [ ]:

np.mean(np.minimum(24, traj_lens)), np.mean(agent_traj_lens)
print((np.minimum(24, traj_lens) == 24).sum())
print((np.array(agent_traj_lens) == 24).sum())

16
18


In [45]:
agent_starting_index_mapping = dict()
agent_end_index_mapping = dict()
for i, response_id in enumerate(agent_full_data.non_tensor_batch['traj_uid']):
    if response_id in agent_starting_index_mapping:
        continue
    ordered_message_tensor_steps = sorted([j for j, res_id in enumerate(agent_full_data.non_tensor_batch['traj_uid']) if res_id == response_id], key=lambda el: agent_full_data.non_tensor_batch['step'][el])
    agent_starting_index_mapping[response_id] = ordered_message_tensor_steps[0]
    agent_end_index_mapping[response_id] = ordered_message_tensor_steps[-1]

agent_starting_index_of_each_traj = list(agent_starting_index_mapping.values())
agent_end_index_of_each_traj = list(agent_end_index_mapping.values())
# why is the verl-agent's fraction successful so low to begin?# success rate: 0.40625 as compared to around 70 for the other multicontext verl setting.
for traj_idx in agent_end_index_of_each_traj:
    if agent_full_data.batch['token_level_scores'][traj_idx].sum(0).item() == -1:
        # on failure
        messages = agent_full_data.non_tensor_batch["raw_prompt"][traj_idx]# .tolist()
        print(len(messages))
        pprint(messages)
# agent_full_data.batch['token_level_scores'].sum(-1)
# ['anchor_obs', 'index', 'data_source', 'uid', 'traj_uid', 'raw_prompt', 'is_action_valid', 'rewards', 'active_masks', 'text_actions', 'step', 'episode_rewards', 'episode_rewards_mean', 'episode_rewards_min', 'episode_rewards_max', 'episode_lengths', 'episode_lengths_mean', 'episode_lengths_min', 'episode_lengths_max', 'success_rate', 'action_generation_failures_success_rate', 'belief_generation_failures_success_rate', 'non_terminal_trajectories_success_rate', 'full_traj_response']
# ['prompts', 'responses', 'input_ids', 'attention_mask', 'ref_log_prob', 'token_level_scores', 'position_ids', 'token_level_rewards', 'response_mask', 'returns', 'rollout_log_probs', 'advantages', 'old_log_probs']

1
array([{'role': 'user', 'content': "You will determine the correct combination of characters at [Position 1, Position 2, Position 3] in a 3-character combination lock through iterative reasoning and queries.\nAll 3 characters are unique.\nThe set of valid characters are as follows: ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']\nEach action is a query of the form ['char 1', 'char 2', 'char 3'].\nEach time you query a combination, you will get feedback from the user about each character: either not in the combination, in the combination but in a different position, or in the combination and in the right position.\nYou can make up to 12 queries.\nYour goal is to find the correct combination in the least number of queries.\nYour current belief state: <belief>characters in the lock: ['0', '6', '7', '9']\n- '0' is in position 1\n- '9' is in position 3\n- '1' and '2' are not in the lock\n- '6' and '7' are not in the lock\n- '7' is not in the lock\n- '3' and '4' are not in the lock</bel

In [7]:
# there is a very minor error it seems that some elements show up twice effectively doubling their gradient. 
# Not sure why exactly. Could be some form of padding. The garbage which I expected to pad every sequence isn't present
# this could be their solution to fixed minibatching. I don't understand their auto padding with dispatch. it calls chunk which doesn't work with I don't think.
len(set(agent_full_data.non_tensor_batch['traj_uid'])), len(set(full_data.non_tensor_batch['request_ids']))

(32, 32)

In [7]:
# np.array([res.count('<action>invalid action</action>\nEnvironment feedback:\nCould not parse') for res in set(agent_full_traj_responses)]).mean()
agent_full_data[0].non_tensor_batch["belief_generation_failures_success_rate"], agent_full_data[0].non_tensor_batch["action_generation_failures_success_rate"]

(np.float64(0.15625), np.float64(3.125))

In [ ]:
starting_index_mapping = dict()
for i, response_id in enumerate(full_data.non_tensor_batch['request_ids']):
    if response_id in starting_index_mapping:
        continue
    starting_index_mapping[response_id] = sorted([j for j, res_id in enumerate(full_data.non_tensor_batch['request_ids']) if res_id == response_id], key=lambda el: full_data.non_tensor_batch['context_indices'][el])[0]

starting_index_of_each_traj = list(starting_index_mapping.values())

# np.mean([stat['trajectory_info']['invalid_format_errors'] for stat in full_data.non_tensor_batch['to_log_stats'][starting_index_of_each_traj]]), np.mean([stat['belief_gen_failures'] for stat in full_data.non_tensor_batch['to_log_stats'][starting_index_of_each_traj]])
# average length on failure
np.mean([stat['trajectory_info']['invalid_format_errors'] for stat in full_data.non_tensor_batch['to_log_stats'][starting_index_of_each_traj]])


(np.float64(2.3125), np.float64(0.15625))

In [8]:
# full_traj_responses
np.array([res.count('<action>invalid action</action>\nEnvironment feedback:\nCould not parse') for res in set(full_traj_responses)]).mean()

np.float64(2.3125)

In [11]:
from pprint import pprint
pprint(list(set(full_traj_responses)))

['<|im_start|>system\n'
 'You will determine the correct combination of characters at [Position 1, '
 'Position 2, Position 3] in a 3-character combination lock through iterative '
 'reasoning and queries.\n'
 'All 3 characters are unique.\n'
 "The set of valid characters are as follows: ['0', '1', '2', '3', '4', '5', "
 "'6', '7', '8', '9']\n"
 "Each action is a query of the form ['char 1', 'char 2', 'char 3'].\n"
 'Each time you query a combination, you will get feedback from the user about '
 'each character: either not in the combination, in the combination but in a '
 'different position, or in the combination and in the right position.\n'
 'You can make up to 12 queries.\n'
 'Your goal is to find the correct combination in the least number of '
 'queries.<|im_end|>\n'
 '<|im_start|>user\n'
 'Give me your first query formatted as a list of 3 characters inside <action> '
 '... </action> after thinking inside <think> ... </think>, e.g., <think> '
 "Let's think step by step before gi

In [ ]:
# it seems hard to count the invalid actions because the model handles them differently in the different environments. 
# In one it lists the previously incorrect action, and in the other it simply says incorrect. 
# This might cause the performance to be higher in the verl codebase, but for the incorrectness not to be penalized as much as it should be early on.

# I'll convert it to be the verl-agent implementation which has the 



In [32]:
from pprint import pprint
pprint(list(set(agent_full_traj_responses)))

['<|im_start|>system\n'
 'You will determine the correct combination of characters at [Position 1, '
 'Position 2, Position 3] in a 3-character combination lock through iterative '
 'reasoning and queries.\n'
 'All 3 characters are unique.\n'
 "The set of valid characters are as follows: ['0', '1', '2', '3', '4', '5', "
 "'6', '7', '8', '9']\n"
 "Each action is a query of the form ['char 1', 'char 2', 'char 3'].\n"
 'Each time you query a combination, you will get feedback from the user about '
 'each character: either not in the combination, in the combination but in a '
 'different position, or in the combination and in the right position.\n'
 'You can make up to 12 queries.\n'
 'Your goal is to find the correct combination in the least number of '
 'queries.<|im_end|>\n'
 '<|im_start|>user\n'
 'Give me your first query formatted as a list of 3 characters inside <action> '
 '... </action> after thinking inside <think> ... </think>, e.g., <think> '
 "Let's think step by step before gi

In [ ]:
# what are the starting statistics of the verl_submodule versus verl-agent?
# verl_submodule:
#   action_generation_failures: 2.3125
#   belief_generation_failures: 0.15625
#   average_length_on_failure:
# verl-agent:
#   action_generation_failures: 3.125 this is average per trajectory. It is slightly higher than the average per trajectory for the 
#   belief_generation_failures: 0.15625
#   average_length_on_failure:
# why are they different?

In [6]:
full_data.non_tensor_batch['to_log_stats'][0]#['invalid_format_errors']
# print(full_data.non_tensor_batch['full_traj_response'][0])
from pprint import pprint
invalid_format_errors_count = []
advantage_weight = []
for full_data_not_completed in ([full_data_i for full_data_i in full_data[torch.tensor(starting_index_of_each_traj)] 
                                if full_data_i.non_tensor_batch['to_log_stats']['trajectory_info']['invalid_format_errors']]):
    pprint(full_data_not_completed.non_tensor_batch['to_log_stats']['trajectory_info'])
    print(full_data_not_completed.batch['token_level_rewards'].sum(-1))
    print(full_data_not_completed.batch['advantages'][0])
    invalid_format_errors_count.append(full_data_not_completed.non_tensor_batch['to_log_stats']['trajectory_info']['invalid_format_errors'])
    advantage_weight.append(full_data_not_completed.batch['advantages'][0].item())
    # print("++++++"*1000)
    # print(full_data_not_completed.non_tensor_batch['full_traj_response'])
    # print(traj_txt)

{'feedback_hist': [('012', [0, 1, 1]),
                   ('100', [2, 0, 0]),
                   ('123', [2, 2, 0]),
                   ('132', [2, 0, 1]),
                   ('120', [2, 2, 0]),
                   ('123', [2, 2, 0]),
                   ('124', [2, 2, 0]),
                   ('124', [2, 2, 0]),
                   ('125', [2, 2, 0]),
                   ('126', [2, 2, 0]),
                   ('127', [2, 2, 2])],
 'invalid_format_errors': 3,
 'repeated_guesses': 19}
tensor(0.1667)
tensor(0.7071)
{'feedback_hist': [('012', [0, 1, 1]),
                   ('312', [0, 1, 1]),
                   ('412', [0, 1, 1]),
                   ('521', [0, 2, 1]),
                   ('623', [0, 2, 0]),
                   ('214', [1, 1, 0]),
                   ('278', [1, 1, 0]),
                   ('103', [2, 0, 0]),
                   ('123', [2, 2, 0]),
                   ('123', [2, 2, 0]),
                   ('123', [2, 2, 0]),
                   ('123', [2, 2, 0])],
 'invalid_format_

In [7]:
# (np.array(advantage_weight) < 0).sum() / len(advantage_weight)

In [8]:
from transformers import AutoModelForCausalLM
model = AutoModelForCausalLM.from_pretrained("qwen/qwen2.5-7b-instruct", device_map='auto')

Sliding Window Attention is enabled but not implemented for `sdpa`; unexpected results may be encountered.


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

In [9]:
total_token_count = full_data.batch['loss_mask'].sum().float()
total_token_count

tensor(203824.)

In [10]:
# repoduce the error in the notebook via a single gradient descent, 
# and test the resulting model with sampling with verl script.
# model = model.cuda()
optim = torch.optim.AdamW(model.parameters(), lr=1e-6)
optim.zero_grad()
total_loss = 0
for i, batch_i in enumerate(tqdm.tqdm(full_data.batch)):
    attention_mask = batch_i['attention_mask'].cuda()
    advantages = batch_i['advantages'].cuda()
    input_ids = batch_i['input_ids'].cuda().long()
    # position_ids = batch_i['position_ids'].cuda()
    loss_mask = batch_i['loss_mask'].cuda()

    bin_att_mask = attention_mask == 1

    input_ids = input_ids[bin_att_mask]
    # position_ids = position_ids[bin_att_mask]
    advantages = advantages[loss_mask[2048:] == 1]
    loss_mask = loss_mask[bin_att_mask]

    out = model(input_ids=input_ids[None])
    logits = out.loss['logits'][0]
    log_prob_action = logits[:-1].log_softmax(-1).gather(-1, input_ids[1:][:, None].long())[:,0][loss_mask[1:]==1] 
    loss = (-log_prob_action * advantages).sum() / total_token_count
    total_loss += loss.item()
    loss.backward()
    # break
optim.step()

  0%|          | 0/1207 [00:00<?, ?it/s]

100%|██████████| 1207/1207 [30:24<00:00,  1.51s/it]


In [11]:
# logits[:-1].log_softmax(-1).gather(-1, input_ids[1:][:, None].long())[:,0][loss_mask[1:]==1] 

In [12]:
# logprobs_from_logits(logits[:-1][None], labels=input_ids[1:][None], inplace_backward=False)[0][loss_mask[1:]==1]

In [13]:
model.save_pretrained("temp_model_save")
tokenizer.save_pretrained("temp_model_save")

('temp_model_save/tokenizer_config.json',
 'temp_model_save/special_tokens_map.json',
 'temp_model_save/vocab.json',
 'temp_model_save/merges.txt',
 'temp_model_save/added_tokens.json',
 'temp_model_save/tokenizer.json')

In [16]:
micro_batches_concated = [b for micro_batches in data_split_micro_batches[0] for b in micro_batches]


In [12]:
min([m['loss_mask'].sum() for m in micro_batches_concated])

tensor(934)

In [13]:
micro_batches_concated_new = []
for mb in micro_batches_concated:
    for j in range(len(mb)):
        micro_batches_concated_new.append(mb[[j]])


# micro_batches_concated = micro_batches_concated_new


In [ ]:
micro_batches_concated[0][]

TensorDict(
    fields={
        advantages: Tensor(shape=torch.Size([8, 2048]), device=cpu, dtype=torch.float32, is_shared=False),
        attention_mask: Tensor(shape=torch.Size([8, 4096]), device=cpu, dtype=torch.int32, is_shared=False),
        input_ids: Tensor(shape=torch.Size([8, 4096]), device=cpu, dtype=torch.int32, is_shared=False),
        loss_mask: Tensor(shape=torch.Size([8, 4096]), device=cpu, dtype=torch.int32, is_shared=False),
        old_log_probs: Tensor(shape=torch.Size([8, 2048]), device=cpu, dtype=torch.float32, is_shared=False),
        position_ids: Tensor(shape=torch.Size([8, 4096]), device=cpu, dtype=torch.int64, is_shared=False),
        ref_log_prob: Tensor(shape=torch.Size([8, 2048]), device=cpu, dtype=torch.float32, is_shared=False),
        responses: Tensor(shape=torch.Size([8, 2048]), device=cpu, dtype=torch.int32, is_shared=False)},
    batch_size=torch.Size([8]),
    device=cpu,
    is_shared=False)

In [24]:
print(tokenizer.decode(input_ids))

<|im_start|>system
You are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>
<|im_start|>user
Global Instruction: You will determine the correct combination of characters at [Position 1, Position 2, Position 3] in a 3-character combination lock through iterative reasoning and queries.
All 3 characters are unique.
The set of valid characters are as follows: ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']
Each action is a query of the form ['char 1', 'char 2', 'char 3'].
Each time you query a combination, you will get feedback from the user about each character: either not in the combination, in the combination but in a different position, or in the combination and in the right position.
You can make up to 12 queries.
Your goal is to find the correct combination in the least number of queries.
Current belief: <belief>Position 1 is '1'.
- Position 2 is '9'.
- Position 3 must be one of the following: ['5', '6', '8'].
- Possible values for Position 3: ['5', '6', '8']

In [1]:
tokenizer.encode

NameError: name 'tokenizer' is not defined

In [23]:
print(tokenizer.chat_template)

{%- if tools %}
    {{- '<|im_start|>system\n' }}
    {%- if messages[0]['role'] == 'system' %}
        {{- messages[0]['content'] }}
    {%- else %}
        {{- 'You are Qwen, created by Alibaba Cloud. You are a helpful assistant.' }}
    {%- endif %}
    {{- "\n\n# Tools\n\nYou may call one or more functions to assist with the user query.\n\nYou are provided with function signatures within <tools></tools> XML tags:\n<tools>" }}
    {%- for tool in tools %}
        {{- "\n" }}
        {{- tool | tojson }}
    {%- endfor %}
    {{- "\n</tools>\n\nFor each function call, return a json object with function name and arguments within <tool_call></tool_call> XML tags:\n<tool_call>\n{\"name\": <function-name>, \"arguments\": <args-json-object>}\n</tool_call><|im_end|>\n" }}
{%- else %}
    {%- if messages[0]['role'] == 'system' %}
        {{- '<|im_start|>system\n' + messages[0]['content'] + '<|im_end|>\n' }}
    {%- else %}
        {{- '<|im_start|>system\nYou are Qwen, created by Alibaba C

In [ ]:
from flash_attn.bert_padding import index_first_axis, pad_input, rearrange, unpad_input
optim = torch.optim.AdamW(model.parameters(), lr=1e-6)
optim.zero_grad()
total_loss = 0

for i, micro_batch_i in enumerate(tqdm.tqdm(micro_batches_concated)):
    attention_mask = micro_batch_i['attention_mask'].cuda()
    advantages = micro_batch_i['advantages'].cuda()
    input_ids = micro_batch_i['input_ids'].cuda().long()
    position_ids = micro_batch_i['position_ids'].cuda()
    loss_mask = micro_batch_i['loss_mask'].cuda()
    responses = micro_batch_i["responses"].cuda()
    response_length = responses.size(-1)
    temperature = 1.0

    batch_size, seqlen = input_ids.shape
    with torch.autocast(device_type='cuda', dtype=torch.bfloat16):
        if True:
            input_ids_rmpad, indices, *_ = unpad_input(input_ids.unsqueeze(-1), attention_mask)  # input_ids_rmpad (total_nnz, ...)
            input_ids_rmpad = input_ids_rmpad.transpose(0, 1)  # (1, total_nnz)

            # unpad the position_ids to align the rotary
            if position_ids.dim() == 3:
                position_ids_rmpad = index_first_axis(rearrange(position_ids, "c b s ... -> (b s) c ..."), indices).transpose(0, 1).unsqueeze(1)  # (3, bsz, seqlen) -> (3, 1, bsz * seqlen)
            else:
                position_ids_rmpad = index_first_axis(rearrange(position_ids.unsqueeze(-1), "b s ... -> (b s) ..."), indices).transpose(0, 1)

            # for compute the log_prob
            input_ids_rmpad_rolled = torch.roll(input_ids_rmpad, shifts=-1, dims=1)  # (1, total_nnz)
            
            input_ids_rmpad_rolled = input_ids_rmpad_rolled.squeeze(0)  # ((total_nnz / sp) + pad)

            output = model(
                input_ids=input_ids_rmpad,
                attention_mask=None,
                position_ids=position_ids_rmpad,
                use_cache=False,
            )
            logits_rmpad = output.logits.squeeze(0)  # (total_nnz, vocab_size)
            logits_rmpad.div_(temperature)

            # if use_sp: ((total_nnz / sp) + pad) ; if not use_sp: (batch, seqlen)
            inplace_backward = True
            inplace_backward = False
            log_probs = logprobs_from_logits(
                logits=logits_rmpad,
                labels=input_ids_rmpad_rolled,
                inplace_backward=inplace_backward,
            )
            full_log_probs = pad_input(
                hidden_states=log_probs.unsqueeze(-1),
                indices=indices,
                batch=batch_size,
                seqlen=seqlen,
            )
            log_probs = full_log_probs.squeeze(-1)[:, -response_length - 1 : -1]
        # else:
        #     output = model(
        #         input_ids=input_ids,
        #         attention_mask=attention_mask,
        #         position_ids=position_ids,
        #         use_cache=False,
        #     )  # prevent model thinks we are generating


        #     logits = output.logits

        #     logits.div_(temperature)
        #     logits = logits[:, -response_length - 1 : -1, :]  # (bsz, response_length, vocab_size)
        #     log_probs = logprobs_from_logits(logits, responses)


    # log_prob_action = logits[:-1].log_softmax(-1).gather(1, input_ids[1:][None].long())[0][loss_mask[1:]==1] 
    
    loss = ((-log_probs * advantages).sum() / total_token_count) # * len(micro_batch_i) / len(micro_batches_concated)
    total_loss += loss.item()
    loss.backward()
    # break

optim.step()

100%|██████████| 1207/1207 [30:09<00:00,  1.50s/it]


In [33]:
(attention_mask.cumsum(-1) -1)[0,:-1857]
position_ids[0, :-1857]
# 2397 - 541

tensor([  0,   0,   0,  ..., 538, 539, 540], device='cuda:0')

$$\nabla\log{p_\theta(a)}$$
does this equal
$$\nabla\exp(\log{p_\theta(a)} - \log{p_\text{old}(a)})$$
when $\log{p_\text{old}(a)}$ is equal to $\log{p_\theta(a)}$?
$$\nabla\exp(\log{p_\theta(a)} - \log{p_\text{old}(a)})$$
$$\exp(\log{p_\theta(a)} - \log{p_\text{old}(a)}) \cdot  \nabla (\log{p_\theta(a)} - \log{p_\text{old}(a)})$$
$$\exp(\log{p_\theta(a)} - \log{p_\text{old}(a)}) \cdot  \nabla \log{p_\theta(a)}$$
$$\exp(0) \cdot  \nabla \log{p_\theta(a)}$$
$$\nabla \log{p_\theta(a)}$$
Yes

In [42]:
# print(tokenizer.batch_decode(input_ids_rmpad[:, 577:1012])[0])

In [54]:
[tokenizer.decode(t) for t in output.loss['logits'][position_ids_rmpad == 0].max(-1).indices]

['0', ' response', 'response', '\n', '\n', '\n', '\n', '\n']

In [ ]:
# output = model(
#     input_ids=input_ids_rmpad,
#     attention_mask=None,
#     position_ids=position_ids_rmpad,
#     use_cache=False,
# )

output2 = model(
    input_ids=input_ids_rmpad[:, 577:1012],
    attention_mask=None,
    position_ids=position_ids_rmpad[:, 577:1012],
    use_cache=False,
)

In [29]:
output2.loss['logits']

tensor([[[ 4.3198,  6.1736,  6.7401,  ..., -3.6970, -3.6969, -3.6970],
         [ 3.1169,  1.8224,  7.6177,  ..., -2.7360, -2.7359, -2.7358],
         [ 3.4046,  5.3615,  7.3856,  ..., -5.5598, -5.5596, -5.5598],
         ...,
         [-2.2117, -7.4690, -4.0653,  ...,  4.0149,  4.0151,  4.0150],
         [ 5.4750, -0.4556,  1.1598,  ...,  3.7543,  3.7546,  3.7547],
         [ 5.2679, -0.6515,  0.5474,  ...,  7.3433,  7.3434,  7.3433]]],
       device='cuda:0', grad_fn=<ToCopyBackward0>)

In [41]:
[tokenizer.decode(t) for t in output2.loss['logits'][0].max(-1).indices]

['0',
 '\n',
 '\n',
 ' are',
 ' a',
 'wen',
 ',',
 ' a',
 ' by',
 ' Alibaba',
 ' Cloud',
 '.',
 ' You',
 ' are',
 ' designed',
 ' Chinese',
 ' and',
 ' with',
 ' User',
 '.system',
 '  \n  \n',
 '\n\n',
 ' Can',
 '我',
 ' are',
 ' now',
 ' the',
 ' most',
 ' answer',
 ' of',
 ' words',
 ' to',
 ' the',
 'X',
 ' X',
 '1',
 '],',
 ' Position',
 ' ',
 '2',
 ',',
 ' Position',
 ' ',
 '3',
 ',',
 ' from',
 ' a',
 ' ',
 '3',
 '-letter',
 ' code',
 ' lock',
 '.',
 ' a',
 ' deduction',
 '.',
 ' deduction',
 '.',
 'The',
 ' characters',
 '3',
 ' characters',
 ' are',
 ' from',
 ' and',
 'The',
 ' characters',
 ' of',
 ' characters',
 ' characters',
 ' is',
 ':',
 ' follows',
 ':',
 ' {',
 'A',
 "',",
 " '",
 '1',
 "',",
 " '",
 '2',
 "',",
 " '",
 '3',
 "',",
 " '",
 '4',
 "',",
 " '",
 '5',
 "',",
 " '",
 '6',
 "',",
 " '",
 '7',
 "',",
 " '",
 '8',
 "',",
 " '",
 '9',
 "',",
 'You',
 ' query',
 ' consists',
 ' a',
 ' guess',
 ' to',
 ' a',
 ' form',
 ' [',
 'a',
 '1',
 '1',
 "',",
 " '",
 'cha

In [17]:
total_loss

-4.520179669605568

In [ ]:
# log_probs.shape
# advantages.shape
# loss

tensor(-0.0669, device='cuda:0', grad_fn=<DivBackward0>)

In [ ]:
model.save_pretrained("temp_model_save_replicate3")
tokenizer.save_pretrained("temp_model_save_replicate3")


('temp_model_save_replicate3/tokenizer_config.json',
 'temp_model_save_replicate3/special_tokens_map.json',
 'temp_model_save_replicate3/vocab.json',
 'temp_model_save_replicate3/merges.txt',
 'temp_model_save_replicate3/added_tokens.json',
 'temp_model_save_replicate3/tokenizer.json')

In [48]:
logits = out.loss['logits'][0] # .shape # [loss_mask==1].shape
[tokenizer.decode(i) for i in input_ids[loss_mask == 1]]
tokenizer.decode(input_ids)
# logits[:-1].gather(1, input_ids[1:][None].long()).cpu()[0][loss_mask[1:].cpu()==1]#[]

# attention_mask.shape
# loss_mask[attention_mask == 1]

"<|im_start|>system\nYou are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>\n<|im_start|>user\nYou will determine the correct combination of characters at [Position 1, Position 2, Position 3] in a 3-character combination lock through iterative reasoning and queries.\nAll 3 characters are unique.\nThe set of valid characters are as follows: ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']\nEach action is a query of the form ['char 1', 'char 2', 'char 3'].\nEach time you query a combination, you will get feedback from the user about each character: either not in the combination, in the combination but in a different position, or in the combination and in the right position.\nYou can make up to 12 queries.\nYour goal is to find the correct combination in the least number of queries.\nYour current belief state: <belief>'1' is in Position 1.\n'2' is in Position 2.\nThe third character must be one of '4', '5', '6', '7', '8', or '9'.</belief>\nYour last action:\n<act

In [49]:
print(tokenizer.decode(batch_i['input_ids']))

<|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|><|endoftext|

In [78]:
tokenizer.batch_decode(tokenizer.apply_chat_template([{'role': 'user', 'content': "what is 2+2?"}], add_generation_prompt=True, return_tensors='pt'))

['<|im_start|>system\nYou are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>\n<|im_start|>user\nwhat is 2+2?<|im_end|>\n<|im_start|>assistant\n']

In [81]:
output = model.generate(tokenizer.apply_chat_template([{'role': 'user', 'content': "what is 2+2?"}], add_generation_prompt=True, return_tensors='pt').cuda())


In [83]:
(tokenizer.decode(output[0], skip_special_tokens=False))

'<|im_start|>system\nYou are Qwen, created by Alibaba Cloud. You are a helpful assistant.<|im_end|>\n<|im_start|>user\nwhat is 2+2?<|im_end|>\n<|im_start|>assistant\n2 + 2 equals 4.<|im_end|>'

In [57]:
help(tokenizer.apply_chat_template)# ([{'role': 'user', 'content': "hello mendes"}], tokenize=False)

Help on method apply_chat_template in module transformers.tokenization_utils_base:

apply_chat_template(conversation: Union[List[Dict[str, str]], List[List[Dict[str, str]]]], tools: Optional[List[Union[Dict, Callable]]] = None, documents: Optional[List[Dict[str, str]]] = None, chat_template: Optional[str] = None, add_generation_prompt: bool = False, continue_final_message: bool = False, tokenize: bool = True, padding: Union[bool, str, transformers.utils.generic.PaddingStrategy] = False, truncation: bool = False, max_length: Optional[int] = None, return_tensors: Union[str, transformers.utils.generic.TensorType, NoneType] = None, return_dict: bool = False, return_assistant_tokens_mask: bool = False, tokenizer_kwargs: Optional[Dict[str, Any]] = None, **kwargs) -> Union[str, List[int], List[str], List[List[int]], transformers.tokenization_utils_base.BatchEncoding] method of transformers.models.qwen2.tokenization_qwen2_fast.Qwen2TokenizerFast instance
    Converts a list of dictionaries wit